In [111]:
import re
from pathlib import Path
import pandas as pd
import pypsa
import numpy as np
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import geopandas as gpd
from __future__ import annotations
from pathlib import Path
from typing import Optional, Union, Dict, Any
import plotly.express as px
import plotly.graph_objects as go
from shapely.geometry import Point, box


### 1. Import network components

In [112]:
from dataclasses import dataclass
from pathlib import Path

@dataclass(frozen=True)
class ScenarioConfig:
    name: str
    inputs_dir: Path         # folder containing buses.csv, powerplant_units.csv, ...
    nc_path: Path            # redispatch_full_redispatch.nc


#### **Example usage: Select scenario configuration**

In [113]:
# Example scenario configurations

# 1. Example 06a - with storage & without transmission expansion
cfg_06a_stor = ScenarioConfig(
    name="example_06a_storage",
    inputs_dir=Path(r"C:\Users\par19744\Python_projects\ASSUME_project\ASSUME_Use_case\2035\assume\examples\inputs\example_06a"),
    nc_path=Path(r"C:\Users\par19744\Python_projects\ASSUME_project\ASSUME_results\Use case results\O45 Strom\with storage\example_06a_base\pypsa_nc\redispatch_full_redispatch.nc"),
)


# 2. Example 06a - with storage & with transmission expansion
cfg_06a_stor_trans = ScenarioConfig(
    name="example_06a_storage_transmission",
    inputs_dir=Path(r"C:\Users\par19744\Python_projects\ASSUME_project\ASSUME_Use_case\2035\assume\examples\inputs\example_06a"),
    nc_path=Path(r"C:\Users\par19744\Python_projects\ASSUME_project\ASSUME_results\Use case results\O45 Strom\with_storage_transmission\example_06a_base\pypsa_nc\redispatch_full_redispatch.nc"),
)


#### Load powerplants, storages and exchange units to create a combined units dataframe

In [114]:
# technology harmonization rules (keep in one place)
POWERPLANT_TECH_MAP = {
    "open cycle gas turbine": "natural gas",
    "gas steam turbine": "natural gas",
    "combined cycle gas turbine": "natural gas",
    "gas engine": "natural gas",
    "small gas mix": "natural gas",
}

def load_scenario_inputs(cfg: ScenarioConfig) -> dict:
    """
    Returns:
      - buses: DataFrame with at least ['bus','bus_id','x','y',...]
      - units: Series mapping unit_id -> technology  (index=unit_id)
      - raw: optional raw dfs if you want them
    """
    p = cfg.inputs_dir

    # --- buses ---
    buses = pd.read_csv(p / "buses.csv")
    # your file uses 'name' -> bus
    if "name" in buses.columns and "bus" not in buses.columns:
        buses = buses.rename(columns={"name": "bus"})
    # ensure types are stable for joins
    if "bus_id" in buses.columns:
        buses["bus_id"] = pd.to_numeric(buses["bus_id"], errors="coerce")

    # --- powerplants ---
    powerplants = pd.read_csv(p / "powerplant_units.csv")
    powerplants = powerplants[["name", "technology"]].rename(columns={"name": "unit_id"})
    powerplants["technology"] = powerplants["technology"].replace(POWERPLANT_TECH_MAP)

    # --- storage ---
    storage_units = pd.read_csv(p / "storage_units.csv")
    storage_units = storage_units[["name", "technology"]].rename(columns={"name": "unit_id"})

    # --- exchange ---
    exchange_units = pd.read_csv(p / "exchange_units.csv")
    exchange_units = exchange_units.rename(columns={"name": "unit_id"})
    exchange_units["technology"] = "exchange_units"
    exchange_units = exchange_units[["unit_id", "technology"]]

    # --- combine ---
    units_df = pd.concat([powerplants, storage_units, exchange_units], ignore_index=True)

    # if duplicate unit_id appears, last wins; you can change policy if needed
    units = units_df.drop_duplicates("unit_id", keep="last").set_index("unit_id")["technology"]

    return {
        "buses": buses,
        "units": units,                  # Series: unit_id -> tech
        "units_df": units_df,            # optional
        "powerplants": powerplants,
        "storage_units": storage_units,
        "exchange_units": exchange_units,
    }


#### Load map box for Plotly plots

In [115]:
def make_germany_nuts3_base_map(
    germany_nuts3: gpd.GeoDataFrame,
    buses_df: pd.DataFrame | gpd.GeoDataFrame | None = None,
    bus_label: str = "bus_id",          # "bus_id" or "bus" or None
    show_bus_labels: bool = True,
    bus_marker_size: int = 6,
    bus_marker_color: str = "gray",
    mapbox_style: str = "carto-positron",
    fill_rgba: str = "rgba(219,238,255,0.35)",
    border_rgba: str = "rgba(0,0,0,0.45)",
    border_width: int = 1,
    height: int = 900,
    width: int = 1000,
    zoom_pad: float = 0.2,
):
    """
    Returns a Plotly Mapbox figure with Germany NUTS3 polygons as background,
    automatically centered/zoomed to Germany extent.
    Optionally overlays buses (points) and labels them.

    buses_df requirements:
      - either columns ['x','y'] in EPSG:4326 (lon/lat), or
      - a GeoDataFrame with geometry, convertible to EPSG:4326.
    """

    # ---- Ensure WGS84 for Mapbox polygons ----
    g_ll = germany_nuts3.to_crs(4326)

    minx, miny, maxx, maxy = g_ll.total_bounds
    center_lon = (minx + maxx) / 2
    center_lat = (miny + maxy) / 2

    # crude zoom heuristic from bbox
    lon_span = maxx - minx
    lat_span = maxy - miny
    span = max(lon_span, lat_span) + zoom_pad
    zoom = float(np.clip(8 - np.log2(span * 10), 4.5, 7.5))

    # ---- Create empty figure ----
    fig = px.scatter_mapbox(
        lat=[],
        lon=[],
        height=height,
        width=width,
        zoom=zoom,
        center={"lat": center_lat, "lon": center_lon},
    )

    # ---- Add NUTS3 polygons as geojson layers ----
    fig.update_layout(
        mapbox_style=mapbox_style,
        mapbox_layers=[
            {
                "sourcetype": "geojson",
                "source": g_ll.__geo_interface__,
                "type": "fill",
                "color": fill_rgba,
                "below": "traces",
            },
            {
                "sourcetype": "geojson",
                "source": g_ll.__geo_interface__,
                "type": "line",
                "color": border_rgba,
                "line": {"width": border_width},
                "below": "traces",
            },
        ],
        margin=dict(l=0, r=0, t=0, b=0),
        dragmode="pan",
    )

    # ---- Add buses as traces (if provided) ----
    if buses_df is not None:
        if isinstance(buses_df, gpd.GeoDataFrame) and "geometry" in buses_df.columns:
            b_ll = buses_df.to_crs(4326).copy()
            b_ll["lon"] = b_ll.geometry.x
            b_ll["lat"] = b_ll.geometry.y
        else:
            # Expect x/y columns. Here we assume x=lon, y=lat already.
            b_ll = buses_df.copy()
            if not {"x", "y"}.issubset(b_ll.columns):
                raise ValueError("buses_df must have columns ['x','y'] or be a GeoDataFrame with geometry.")
            b_ll["lon"] = pd.to_numeric(b_ll["x"], errors="coerce")
            b_ll["lat"] = pd.to_numeric(b_ll["y"], errors="coerce")

        b_ll = b_ll.dropna(subset=["lon", "lat"]).copy()

        # Decide label text
        label_text = None
        if show_bus_labels and bus_label is not None and bus_label in b_ll.columns:
            label_text = b_ll[bus_label].astype(str)

        # Marker trace
        fig.add_trace(go.Scattermapbox(
            lat=b_ll["lat"],
            lon=b_ll["lon"],
            mode="markers",
            name="Buses",
            marker=dict(size=bus_marker_size, color=bus_marker_color, opacity=0.9),
            hovertext=b_ll.get("bus_id", b_ll.get("bus", "")).astype(str) if ("bus_id" in b_ll.columns or "bus" in b_ll.columns) else None,
            hoverinfo="text",
            showlegend=True,
        ))

        # Optional labels trace
        if label_text is not None:
            fig.add_trace(go.Scattermapbox(
                lat=b_ll["lat"],
                lon=b_ll["lon"],
                mode="text",
                text=label_text,
                textposition="top center",
                textfont=dict(size=10, color="black"),
                name="Bus labels",
                hoverinfo="skip",
                showlegend=False,
            ))

    return fig, {"center_lat": center_lat, "center_lon": center_lon, "zoom": zoom}


eu = gpd.read_file(r"C:\Users\par19744\Python_projects\ASSUME_project\Powerplant_data_clean\GIS\shapefile_data\NUTS3_2013\NUTS_RG_03M_2013_4326_LEVL_0.shp.zip")
germany_nuts3 = eu[eu["CNTR_CODE"] == "DE"].copy()

scenario_data = load_scenario_inputs(cfg_06a_stor)
buses_df = scenario_data["buses"][["bus_id", "bus", "x", "y"]].copy()

# Create base map + buses (labels by bus_id)
fig_map, view = make_germany_nuts3_base_map(
    germany_nuts3,
    buses_df=buses_df,
    bus_label="bus_id",
    show_bus_labels=True,
    height=400,
    width=500,
)

fig_map.update_layout(legend=dict(title="Germany NUTS3 + Buses"))
fig_map.show(config={"scrollZoom": True})

### 2. Redispatch Visualization

#### A) Redispatch from real units

In [116]:
def _base_unit_id(gen_name: str) -> str:
    """
    Strip common suffixes added by redispatch/backups.
    Extend this if your naming differs.
    """
    return re.sub(r"(_up|_down)$", "", str(gen_name))

def load_redispatch_summary(
    nc_path: str | Path,
    units: pd.DataFrame | pd.Series | None = None,
    tech_col: str = "technology",
    storage_techs: set[str] | None = None,
) -> dict:
    """
    Loads a PyPSA netcdf and returns:
      - n: pypsa.Network
      - summary: time series totals and storage split
      - up_by_tech, dn_by_tech: time series per technology (if units provided)
    """

    nc_path = Path(nc_path)
    n = pypsa.Network()
    n.import_from_netcdf(str(nc_path))

    # --- split generators_t.p into up/down by column naming convention ---
    gen_p = n.generators_t.p.copy()
    up_cols = [c for c in gen_p.columns if str(c).endswith("_up")]
    dn_cols = [c for c in gen_p.columns if str(c).endswith("_down")]

    up = gen_p[up_cols] if up_cols else pd.DataFrame(index=n.snapshots)
    dn = gen_p[dn_cols] if dn_cols else pd.DataFrame(index=n.snapshots)

    up_total = up.sum(axis=1)
    dn_total = dn.sum(axis=1)

    # --- attach technology mapping (optional but recommended) ---
    up_by_tech = None
    dn_by_tech = None
    up_storage = pd.Series(0.0, index=n.snapshots)
    dn_storage = pd.Series(0.0, index=n.snapshots)

    if storage_techs is None:
        storage_techs = {"PSPP", "li_ion_battery", "compressed_air_storage"}

    if units is not None:
        # units can be a DataFrame with column 'technology' indexed by unit_id,
        # OR a Series mapping unit_id -> technology
        if isinstance(units, pd.DataFrame):
            tech_map = units[tech_col]
        else:
            tech_map = units  # Series

        n.generators["base_unit_id"] = n.generators.index.to_series().map(_base_unit_id)
        n.generators["technology"] = n.generators["base_unit_id"].map(tech_map)

        tech = n.generators["technology"]

        # group by technology, dropping columns where technology is NaN
        up_by_tech = up.groupby(tech.reindex(up.columns), axis=1).sum() if not up.empty else pd.DataFrame(index=n.snapshots)
        dn_by_tech = dn.groupby(tech.reindex(dn.columns), axis=1).sum() if not dn.empty else pd.DataFrame(index=n.snapshots)

        # storage split
        if not up_by_tech.empty:
            up_storage = up_by_tech.loc[:, up_by_tech.columns.intersection(storage_techs)].sum(axis=1)
        if not dn_by_tech.empty:
            dn_storage = dn_by_tech.loc[:, dn_by_tech.columns.intersection(storage_techs)].sum(axis=1)

    summary = pd.DataFrame(
        {
            "up_total_MW": up_total,
            "down_total_MW": dn_total,
            "up_storage_MW": up_storage,
            "down_storage_MW": dn_storage,
            "up_non_storage_MW": up_total - up_storage,
            "down_non_storage_MW": dn_total - dn_storage,
        },
        index=n.snapshots,
    )

    return {
        "network": n,
        "summary": summary,
        "up_by_tech": up_by_tech,
        "dn_by_tech": dn_by_tech,
        "path": str(nc_path),
    }


In [117]:
def run_scenario(cfg: ScenarioConfig, storage_techs=None) -> dict:
    inputs = load_scenario_inputs(cfg)
    redispatch = load_redispatch_summary(cfg.nc_path, units=inputs["units"], storage_techs=storage_techs)

    return {
        "cfg": cfg,
        "inputs": inputs,
        "redispatch": redispatch,
    }


#### **Example usage: Redispatch volumes**

In [118]:
res_06a_stor = run_scenario(cfg_06a_stor)
res_06a_stor["redispatch"]["summary"].head()

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1997313739.py:59: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1997313739.py:60: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



up_total_MW  down_total_MW  up_storage_MW  down_storage_MW  \
snapshot                                                                
0          5900.964592   89805.931548    4923.443873      3414.837062   
1           871.588514   96757.475770      12.981683         0.000000   
2         20444.556786   25019.851136   18655.952959      2130.451879   
3         25752.578569   25752.578569   22193.207279      3779.572696   
4         26552.972893   26552.972893   23559.669620      1874.785228   

          up_non_storage_MW  down_non_storage_MW  
snapshot                                          
0                977.520719         86391.094487  
1                858.606832         96757.475770  
2               1788.603827         22889.399256  
3               3559.371290         21973.005873  
4               2993.303273         24678.187665

In [119]:
res_06a_stor_trans = run_scenario(cfg_06a_stor_trans)
res_06a_stor_trans["redispatch"]["summary"].head()

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1997313739.py:59: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1997313739.py:60: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



up_total_MW  down_total_MW  up_storage_MW  down_storage_MW  \
snapshot                                                                
0         25687.559733   11425.870704   23264.497867      4137.951492   
1          3456.293998  108318.223437    3265.038486      3273.611982   
2         26648.960516   17517.953184   23924.321369      3491.474149   
3         28729.596846   17167.997471   25859.265320      4906.384676   
4         34732.036630   24720.506205   30435.901448      2806.458356   

          up_non_storage_MW  down_non_storage_MW  
snapshot                                          
0               2423.061866          7287.919212  
1                191.255513        105044.611456  
2               2724.639147         14026.479035  
3               2870.331526         12261.612795  
4               4296.135182         21914.047849

##### **Upward and downward redispatch by Bus**

In [120]:
def redispatch_by_bus(n, threshold=0.0):
    """
    Aggregate redispatch by bus (totals over time).
    Returns DataFrame: bus, up_total, down_total, lon, lat
    """

    gen_p = n.generators_t.p

    up_cols = [c for c in gen_p.columns if str(c).endswith("_up")]
    dn_cols = [c for c in gen_p.columns if str(c).endswith("_down")]

    # Use only existing cols (defensive)
    up_cols = [c for c in up_cols if c in gen_p.columns]
    dn_cols = [c for c in dn_cols if c in gen_p.columns]

    # Positive-only (in case sign conventions differ)
    up = gen_p[up_cols].clip(lower=0) if up_cols else pd.DataFrame(index=n.snapshots)
    dn = gen_p[dn_cols].clip(lower=0) if dn_cols else pd.DataFrame(index=n.snapshots)

    # Map each redispatch generator to its bus
    if up_cols:
        up_by_bus_ts = up.groupby(n.generators.loc[up_cols, "bus"].astype(str).str.strip(), axis=1).sum()
        up_total = up_by_bus_ts.sum(axis=0)
    else:
        up_total = pd.Series(dtype=float)

    if dn_cols:
        dn_by_bus_ts = dn.groupby(n.generators.loc[dn_cols, "bus"].astype(str).str.strip(), axis=1).sum()
        dn_total = dn_by_bus_ts.sum(axis=0)
    else:
        dn_total = pd.Series(dtype=float)

    buses = up_total.index.union(dn_total.index)
    df = pd.DataFrame({
        "bus": buses.astype(str),
        "up_total": up_total.reindex(buses).fillna(0.0).values,
        "down_total": dn_total.reindex(buses).fillna(0.0).values,
    })

    # threshold: keep buses where either direction is significant
    if threshold and threshold > 0:
        df = df[(df["up_total"] > threshold) | (df["down_total"] > threshold)].copy()

    # attach coordinates from n.buses (robust reset_index)
    bus_coords = n.buses[["x", "y"]].copy().reset_index()
    idx_col = bus_coords.columns[0]
    bus_coords = bus_coords.rename(columns={idx_col: "bus", "x": "lon", "y": "lat"})
    bus_coords["bus"] = bus_coords["bus"].astype(str).str.strip()

    df["bus"] = df["bus"].astype(str).str.strip()
    df = df.merge(bus_coords, on="bus", how="left").dropna(subset=["lon", "lat"])

    return df


In [121]:
rd_bus_df = redispatch_by_bus(n, threshold=1e2)
rd_bus_df.head()

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:22: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:28: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



bus      up_total     down_total        lon        lat
0    DE1-220  58982.523064   91648.782266  13.677140  54.817281
1   DE10-380  37065.976264  116538.878722   9.552734  53.563511
2  DE100-220  41502.983142    6751.386829   7.135589  51.417065
3  DE100-380  34029.896965   10496.900615   7.135882  51.417263
4  DE102-220  49893.909873    8235.916125   7.244494  51.400745

##### **Plot upward and downward redispatch**

In [122]:
def add_redispatch_layers(
    fig_map,
    df_bus,
    up_color="#1f77b4",
    dn_color="#e75480",
    rmin=6,
    rmax=26,
    legend_up="Redispatch UP",
    legend_dn="Redispatch DOWN",
):
    """
    Add two bubble layers (up and down) to an existing fig_map.
    Bubble size uses sqrt scaling so area ~ magnitude.
    """

    df_bus = df_bus.copy()
    df_bus["up_total"] = pd.to_numeric(df_bus["up_total"], errors="coerce").fillna(0.0)
    df_bus["down_total"] = pd.to_numeric(df_bus["down_total"], errors="coerce").fillna(0.0)

    # size scaling separately for up and down
    up = df_bus["up_total"].clip(lower=0)
    dn = df_bus["down_total"].clip(lower=0)

    up_max = float(up.max()) if up.max() > 0 else 0.0
    dn_max = float(dn.max()) if dn.max() > 0 else 0.0

    up_size = (rmin + (np.sqrt(up) / np.sqrt(up_max)) * (rmax - rmin)) if up_max > 0 else np.full(len(df_bus), rmin)
    dn_size = (rmin + (np.sqrt(dn) / np.sqrt(dn_max)) * (rmax - rmin)) if dn_max > 0 else np.full(len(df_bus), rmin)

    # --- UP ---
    df_up = df_bus[df_bus["up_total"] > 0].copy()
    if not df_up.empty:
        sizes_up = up_size[df_up.index]

        fig_map.add_trace(go.Scattermapbox(
            lat=df_up["lat"], lon=df_up["lon"],
            mode="markers",
            marker=dict(size=(sizes_up + 2), color="black", opacity=1.0),
            hoverinfo="skip",
            showlegend=False,
        ))

        fig_map.add_trace(go.Scattermapbox(
            lat=df_up["lat"], lon=df_up["lon"],
            mode="markers",
            name=legend_up,
            marker=dict(size=sizes_up, color=up_color, opacity=0.9),
            customdata=np.c_[df_up["bus"].values, df_up["up_total"].values],
            hovertemplate="<b>bus: %{customdata[0]}</b><br>UP: %{customdata[1]:,.3f}<extra></extra>",
            showlegend=True,
        ))

    # --- DOWN ---
    df_dn = df_bus[df_bus["down_total"] > 0].copy()
    if not df_dn.empty:
        sizes_dn = dn_size[df_dn.index]

        fig_map.add_trace(go.Scattermapbox(
            lat=df_dn["lat"], lon=df_dn["lon"],
            mode="markers",
            marker=dict(size=(sizes_dn + 2), color="black", opacity=1.0),
            hoverinfo="skip",
            showlegend=False,
        ))

        fig_map.add_trace(go.Scattermapbox(
            lat=df_dn["lat"], lon=df_dn["lon"],
            mode="markers",
            name=legend_dn,
            marker=dict(size=sizes_dn, color=dn_color, opacity=0.9),
            customdata=np.c_[df_dn["bus"].values, df_dn["down_total"].values],
            hovertemplate="<b>bus: %{customdata[0]}</b><br>DOWN: %{customdata[1]:,.3f}<extra></extra>",
            showlegend=True,
        ))

    return fig_map


##### **Example usage: Upward & downward redispatch**

In [123]:
# Load network (or use your sliced network)
n = pypsa.Network()
n.import_from_netcdf(str(cfg_06a_stor.nc_path))

# Build redispatch bus aggregation
rd_bus_df = redispatch_by_bus(n, threshold=0)

# Overlay up/down redispatch
fig_map = add_redispatch_layers(fig_map, rd_bus_df, up_color="#1f77b4", dn_color="#e75480")

fig_map.update_layout(
    legend=dict(title="Redispatch by bus (UP/DOWN)"),
    width=900,
    height=800
)
fig_map.show(config={"scrollZoom": True})


Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:22: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:28: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



In [124]:
# Load network (or use your sliced network)
n = pypsa.Network()
n.import_from_netcdf(str(cfg_06a_stor_trans.nc_path))

# Build redispatch bus aggregation
rd_bus_df = redispatch_by_bus(n, threshold=0)

# Overlay up/down redispatch
fig_map = add_redispatch_layers(fig_map, rd_bus_df, up_color="#1f77b4", dn_color="#e75480")

fig_map.update_layout(
    legend=dict(title="Redispatch by bus (UP/DOWN)"),
    width=900,
    height=800
)
fig_map.show(config={"scrollZoom": True})

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:22: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\3487328546.py:28: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



#### B) Redispatch from Backup units

##### **Retrieving backup dispatch from PyPSA network**

In [125]:
def backup_redispatch_viz(
    n: Optional[pypsa.Network] = None,
    nc_path: Optional[Union[str, Path]] = None,
    buses_csv: Optional[pd.DataFrame] = None,
    backup_pattern: str = "backup",
    threshold_total: float = 0.5e6,
    size_max: int = 35,
    title: str = "",
    mapbox_style: str = "carto-positron",
    zoom: float = 5,
    show_labels: bool = True,
) -> Dict[str, Any]:
    """
    Visualize backup redispatch (positive dispatch) aggregated by bus.

    Parameters
    ----------
    n : pypsa.Network, optional
        Pre-loaded network. If not provided, nc_path must be provided.
    nc_path : str|Path, optional
        Path to .nc file; used if n is None.
    buses_csv : DataFrame, optional
        Scenario inputs buses table (ASSUME buses.csv). If provided and has columns
        ['bus','bus_id'] (or ['name','bus_id']), bus_id will be joined to plot_df.
    backup_pattern : str
        Substring used to identify backup generators in n.generators.index.
    threshold_total : float
        Filter buses with total backup dispatch > threshold_total.
    size_max : int
        Maximum marker size in Plotly.
    title : str
        Figure title prefix.
    mapbox_style : str
        Mapbox style (e.g. 'carto-positron', 'open-street-map', ...).
    zoom : float
        Initial zoom for the map.
    show_labels : bool
        If True, prints bus name as permanent text on the map.

    Returns
    -------
    dict containing:
      - network
      - backup_gens (DataFrame)
      - backup_dispatch_by_bus_ts (DataFrame): snapshots x buses
      - total_backup_dispatch (Series): total per bus
      - total_backup_dispatch_big (Series): filtered totals
      - plot_df (DataFrame): bus, backup_dispatch, lon, lat, (optional bus_id)
      - fig_map (plotly Figure)
      - fig_bar (plotly Figure)
    """

    # ----------------------------
    # Load network (if needed)
    # ----------------------------
    if n is None:
        if nc_path is None:
            raise ValueError("Provide either a pypsa.Network (n=...) or a netcdf path (nc_path=...).")
        n = pypsa.Network()
        n.import_from_netcdf(str(nc_path))

    # ----------------------------
    # Select backup generators
    # ----------------------------
    gens = n.generators
    mask = gens.index.to_series().astype(str).str.contains(backup_pattern, na=False)
    backup_gens = gens.loc[mask].copy()

    if backup_gens.empty:
        raise ValueError(f"No generators found with pattern '{backup_pattern}' in n.generators.index.")

    # ----------------------------
    # Dispatch time series (positive only)
    # ----------------------------
    p_backup = n.generators_t.p[backup_gens.index].copy()
    p_backup_pos = p_backup.clip(lower=0)

    # Aggregate by bus
    buses_for_gens = n.generators.loc[backup_gens.index, "bus"].astype(str).str.strip()
    backup_dispatch_by_bus_ts = p_backup_pos.groupby(buses_for_gens, axis=1).sum()

    # Totals by bus (sum across snapshots)
    total_backup_dispatch = backup_dispatch_by_bus_ts.sum(axis=0).sort_values(ascending=False)

    # Filter big buses
    total_backup_dispatch_big = total_backup_dispatch[total_backup_dispatch > threshold_total]
    # normalize index strings for safe merge
    total_backup_dispatch_big.index = total_backup_dispatch_big.index.astype(str).str.strip()

    # If nothing passes the threshold, return early with helpful message
    if total_backup_dispatch_big.empty:
        # Create empty figures/dataframes but still return the computed objects
        plot_df = pd.DataFrame(columns=["bus", "backup_dispatch", "lon", "lat"])
        fig_bar = px.bar(title=(title + " – No buses above threshold" if title else "No buses above threshold"))
        fig_map = px.scatter_mapbox(plot_df, lat="lat", lon="lon", title=(title + " – No data" if title else "No data"))
        fig_map.update_layout(mapbox_style=mapbox_style)
        return {
            "network": n,
            "backup_gens": backup_gens,
            "backup_dispatch_by_bus_ts": backup_dispatch_by_bus_ts,
            "total_backup_dispatch": total_backup_dispatch,
            "total_backup_dispatch_big": total_backup_dispatch_big,
            "plot_df": plot_df,
            "fig_map": fig_map,
            "fig_bar": fig_bar,
        }

    # ----------------------------
    # Coordinates from PyPSA buses (robust)
    # ----------------------------
    if not {"x", "y"}.issubset(n.buses.columns):
        raise ValueError("n.buses does not contain 'x' and 'y' columns needed for mapping.")

    bus_coords = n.buses[["x", "y"]].copy().reset_index()

    # first column after reset_index is the former index (bus name), regardless of its label
    idx_col = bus_coords.columns[0]
    bus_coords = bus_coords.rename(columns={idx_col: "bus", "x": "lon", "y": "lat"})
    bus_coords["bus"] = bus_coords["bus"].astype(str).str.strip()

    # ----------------------------
    # Build plotting dataframe
    # ----------------------------
    plot_df = (
        total_backup_dispatch_big.rename("backup_dispatch")
        .reset_index()
        .rename(columns={"index": "bus"})
    )
    plot_df["bus"] = plot_df["bus"].astype(str).str.strip()

    plot_df = plot_df.merge(bus_coords, on="bus", how="left")

    # Drop rows without coordinates
    plot_df = plot_df.dropna(subset=["lon", "lat"]).copy()

    # ----------------------------
    # Optional: attach bus_id from scenario buses.csv
    # ----------------------------
    if buses_csv is not None:
        buses2 = buses_csv.copy()

        # normalize bus column name
        if "bus" not in buses2.columns and "name" in buses2.columns:
            buses2 = buses2.rename(columns={"name": "bus"})

        if "bus" in buses2.columns:
            buses2["bus"] = buses2["bus"].astype(str).str.strip()

        if {"bus", "bus_id"}.issubset(buses2.columns):
            plot_df = plot_df.merge(buses2[["bus", "bus_id"]], on="bus", how="left")

    # ----------------------------
    # Bar figure
    # ----------------------------
    bar_df = total_backup_dispatch_big.rename("backup_dispatch").reset_index().rename(columns={"index": "bus"})
    fig_bar = px.bar(
        bar_df,
        x="bus",
        y="backup_dispatch",
        title=(title + " – Backup dispatch by bus (filtered)" if title else "Backup dispatch by bus (filtered)"),
    )
    fig_bar.update_layout(xaxis_tickangle=-45)

    # ----------------------------
    # Map figure
    # ----------------------------
    hover_data = {"backup_dispatch": ":.3e", "lat": False, "lon": False}
    if "bus_id" in plot_df.columns:
        hover_data["bus_id"] = True

    fig_map = px.scatter_mapbox(
        plot_df,
        lat="lat",
        lon="lon",
        size="backup_dispatch",
        size_max=size_max,
        hover_name="bus",
        hover_data=hover_data,
        zoom=zoom,
        height=900,
        title=(title + " – Backup dispatch map" if title else "Backup dispatch map"),
    )

    if show_labels and not plot_df.empty:
        fig_map.update_traces(
            mode="markers+text",
            text=plot_df["bus"],
            textposition="top center",
        )

    fig_map.update_layout(mapbox_style=mapbox_style, margin=dict(l=0, r=0, t=40, b=0))

    return {
        "network": n,
        "backup_gens": backup_gens,
        "backup_dispatch_by_bus_ts": backup_dispatch_by_bus_ts,
        "total_backup_dispatch": total_backup_dispatch,
        "total_backup_dispatch_big": total_backup_dispatch_big,
        "plot_df": plot_df,
        "fig_map": fig_map,
        "fig_bar": fig_bar,
    }


##### **Examples usage of backup_redispatch**

In [126]:
# 1) load scenario inputs (this defines buses)
inputs = load_scenario_inputs(cfg_06a_stor_trans)
buses = inputs["buses"]   # <-- define buses in the notebook scope

# 2) run visualization by letting the function load the network from nc
out = backup_redispatch_viz(
    nc_path=cfg_06a_stor_trans.nc_path,     # <-- no need for n
    buses_csv=buses,
    threshold_total=1e4,
    title="O45 with storage – example_06a",
)
out["fig_bar"].show()
total_backup_dispatch=out["total_backup_dispatch"]
display(total_backup_dispatch.head(2))

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\316895792.py:80: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



bus
way/50729129-220     750945.762077
way/152261133-220    346794.600345
dtype: float64

##### **Backup redispatch by Bus** 

In [127]:
def backup_redispatch_by_bus(n, threshold=0.0):
    """
    Returns DataFrame with columns:
      bus, up_total, down_total, lon, lat
    where up_total/down_total are summed over time (MW-sum; use weightings if needed).
    """
    # backup generators (base name includes 'backup')
    gens_backup = n.generators.index[n.generators.index.to_series().astype(str).str.contains("backup", na=False)]

    # split into up/down redispatch generators
    up_gens = [g for g in gens_backup if str(g).endswith("_up")]
    dn_gens = [g for g in gens_backup if str(g).endswith("_down")]

    up = n.generators_t.p[up_gens].clip(lower=0) if up_gens else pd.DataFrame(index=n.snapshots)
    dn = n.generators_t.p[dn_gens].clip(lower=0) if dn_gens else pd.DataFrame(index=n.snapshots)

    # aggregate by bus
    if not up.empty:
        up_by_bus = up.groupby(n.generators.loc[up.columns, "bus"], axis=1).sum()
        up_total = up_by_bus.sum(axis=0)
    else:
        up_total = pd.Series(dtype=float)

    if not dn.empty:
        dn_by_bus = dn.groupby(n.generators.loc[dn.columns, "bus"], axis=1).sum()
        dn_total = dn_by_bus.sum(axis=0)
    else:
        dn_total = pd.Series(dtype=float)


    # align both series to same bus index
    buses = up_total.index.union(dn_total.index)
    df = pd.DataFrame({
        "bus": buses.astype(str),
        "up_total": up_total.reindex(buses).fillna(0.0).values,
        "down_total": dn_total.reindex(buses).fillna(0.0).values,
    })

    # optional thresholding (keep buses where either direction exceeds threshold)
    if threshold and threshold > 0:
        df = df[(df["up_total"] > threshold) | (df["down_total"] > threshold)].copy()

    # attach coordinates from n.buses
    bus_coords = n.buses[["x", "y"]].copy().reset_index()
    idx_col = bus_coords.columns[0]
    bus_coords = bus_coords.rename(columns={idx_col: "bus", "x": "lon", "y": "lat"})
    bus_coords["bus"] = bus_coords["bus"].astype(str).str.strip()

    df["bus"] = df["bus"].astype(str).str.strip()
    df = df.merge(bus_coords, on="bus", how="left").dropna(subset=["lon", "lat"])

    return df


##### **Plot backup redispatch by bus in a map**

In [128]:
def add_backup_redispatch_layers(fig_map, backup_bus_df,
                                up_color="#1f77b4", dn_color="#e75480",
                                rmin=6, rmax=26,
                                show_labels=False):
    """
    Adds 2 layers: Upward backup redispatch and Downward backup redispatch.
    Size is proportional to sqrt(value) to make bubble area proportional to MW.
    """

    # sizes
    up = backup_bus_df["up_total"].astype(float).clip(lower=0)
    dn = backup_bus_df["down_total"].astype(float).clip(lower=0)

    # scale each direction separately (more readable)
    up_max = float(up.max()) if up.max() > 0 else 0.0
    dn_max = float(dn.max()) if dn.max() > 0 else 0.0

    up_size = (rmin + (np.sqrt(up) / np.sqrt(up_max)) * (rmax - rmin)) if up_max > 0 else np.full(len(up), rmin)
    dn_size = (rmin + (np.sqrt(dn) / np.sqrt(dn_max)) * (rmax - rmin)) if dn_max > 0 else np.full(len(dn), rmin)

    # --------- UPWARD (backup_up) ----------
    df_up = backup_bus_df[backup_bus_df["up_total"] > 0].copy()
    if not df_up.empty:
        sizes_up = up_size[df_up.index]

        # outline
        fig_map.add_trace(go.Scattermapbox(
            lat=df_up["lat"], lon=df_up["lon"],
            mode="markers",
            name=None, showlegend=False,
            marker=dict(size=(sizes_up + 2), color="black", opacity=1.0),
            hoverinfo="skip",
        ))

        # fill
        fig_map.add_trace(go.Scattermapbox(
            lat=df_up["lat"], lon=df_up["lon"],
            mode="markers",
            name="Backup redispatch UP",
            marker=dict(size=sizes_up, color=up_color, opacity=0.9),
            customdata=np.c_[df_up["bus"].values, df_up["up_total"].values],
            hovertemplate="<b>%{customdata[0]}</b><br>Backup UP: %{customdata[1]:,.3f}<extra></extra>",
        ))

    # --------- DOWNWARD (backup_down) ----------
    df_dn = backup_bus_df[backup_bus_df["down_total"] > 0].copy()
    if not df_dn.empty:
        sizes_dn = dn_size[df_dn.index]

        # outline
        fig_map.add_trace(go.Scattermapbox(
            lat=df_dn["lat"], lon=df_dn["lon"],
            mode="markers",
            name=None, showlegend=False,
            marker=dict(size=(sizes_dn + 2), color="black", opacity=1.0),
            hoverinfo="skip",
        ))

        # fill
        fig_map.add_trace(go.Scattermapbox(
            lat=df_dn["lat"], lon=df_dn["lon"],
            mode="markers",
            name="Backup redispatch DOWN",
            marker=dict(size=sizes_dn, color=dn_color, opacity=0.9),
            customdata=np.c_[df_dn["bus"].values, df_dn["down_total"].values],
            hovertemplate="<b>%{customdata[0]}</b><br>Backup DOWN: %{customdata[1]:,.3f}<extra></extra>",
        ))

    if show_labels:
        fig_map.add_trace(go.Scattermapbox(
            lat=backup_bus_df["lat"], lon=backup_bus_df["lon"],
            mode="text",
            text=backup_bus_df["bus"].astype(str),
            textposition="top center",
            hoverinfo="skip",
            showlegend=False
        ))

    return fig_map

##### **Example usage: Backup redispatch in a map**

In [129]:
def slice_network_snapshots(n_full: pypsa.Network, n_snapshots: int) -> pypsa.Network:
    """
    Return a copy of n_full restricted to the first n_snapshots snapshots,
    slicing all *_t panels consistently.
    """
    n = n_full.copy()

    snapshots_sel = n.snapshots[:n_snapshots]
    n.snapshots = snapshots_sel

    # slice snapshot weightings too (important)
    if hasattr(n, "snapshot_weightings") and n.snapshot_weightings is not None:
        n.snapshot_weightings = n.snapshot_weightings.loc[snapshots_sel]

    # slice all time-dependent panels
    for c in n.iterate_components():
        # c.pnl is a dict of DataFrames indexed by snapshots
        for k, df in c.pnl.items():
            if df is not None and len(df.index) > 0:
                c.pnl[k] = df.loc[snapshots_sel]

    return n

##### **1. Scenario O45 Strom: Storage: 2035**

In [130]:
# Load full network
n_full = pypsa.Network()
n_full.import_from_netcdf(str(cfg_06a_stor.nc_path))

# Slice the network in order to have fair comparison with smaller runs
n = slice_network_snapshots(n_full, 4296)

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='Load')


In [131]:
backup_bus_df = backup_redispatch_by_bus(n, threshold=1e2)
fig_map = add_backup_redispatch_layers(fig_map, backup_bus_df,up_color="#1f77b4",dn_color="#e75480")
fig_map.update_layout(
    legend=dict(title="Backup units redispatch"),
    width=900,
    height=800
)
fig_map.show(config={"scrollZoom": True})

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1253967699.py:19: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1253967699.py:25: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



##### **2. Scenario O45 Strom: Storage + Transmission: 2035**

In [133]:
n = pypsa.Network()
n.import_from_netcdf(str(cfg_06a_stor_trans.nc_path))
backup_bus_df = backup_redispatch_by_bus(n, threshold=1e2)
fig_map = add_backup_redispatch_layers(fig_map, backup_bus_df,up_color="#1f77b4",dn_color="#e75480")
fig_map.update_layout(
    legend=dict(title="Backup units redispatch"),
    width=900,
    height=800
)
fig_map.show(config={"scrollZoom": True})

Index(['demand_CRM_pos', 'demand_CRM_neg'], dtype='object', name='name')
INFO:pypsa.io:Imported network redispatch_full_redispatch.nc has buses, carriers, generators, lines, loads
C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1253967699.py:19: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

C:\Users\par19744\AppData\Local\Temp\ipykernel_33500\1253967699.py:25: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.

